In [1]:
import numpy as np
from numpy import genfromtxt
from itertools import combinations
import torch
import math 
from torch import nn
import torch.nn.functional as F
import torch.optim as optim
import matplotlib.pyplot as plt

In [2]:
#data = genfromtxt('small_file_correct_coord.txt', delimiter=',')
data = genfromtxt('test_output_false_negative.txt', delimiter=',')
#data = genfromtxt('small_file.txt', delimiter=',')
#data = genfromtxt('raw_data_test.txt',delimiter=',') ## raw not preclustered data
data[:,4] =(data[:,4]-np.min(data[:,4]))/(np.max(data[:,4])-np.min(data[:,4]))
print(data)

[[ 0.00000000e+00  1.12801600e+00  9.13283000e-01 -2.69977000e+00
   3.20532033e-01]
 [ 1.00000000e+00  9.52915000e-01  5.19144000e-01  8.78809000e-01
   9.30878204e-01]
 [ 1.00000000e+00  4.34082000e-01  5.67670000e-01 -2.31193600e+00
   9.16612795e-01]
 ...
 [ 9.71800000e+03  2.11805000e+00  6.91111000e-01  1.31600900e+00
   5.89230502e-01]
 [ 9.71900000e+03  1.61018700e+00  1.01372300e+00  2.24618800e+00
   5.36947139e-01]
 [ 9.71900000e+03  1.41488000e-01  1.47488600e+00 -4.42010000e-01
   5.20508288e-01]]


#### this step is only needed if you use non preclustered input data

In [3]:
unique_values, continuous_numbers = np.unique(data[:,0], return_inverse=True)
data[:,0] = continuous_numbers
data[:,2] = data[:,2]*math.pi/180.
data[:,3] = data[:,3]*math.pi/180.
print(continuous_numbers)
print(data)


[   0    1    1 ... 9718 9719 9719]
[[ 0.00000000e+00  1.12801600e+00  1.59397954e-02 -4.71198755e-02
   3.20532033e-01]
 [ 1.00000000e+00  9.52915000e-01  9.06077209e-03  1.53381105e-02
   9.30878204e-01]
 [ 1.00000000e+00  4.34082000e-01  9.90771056e-03 -4.03508953e-02
   9.16612795e-01]
 ...
 [ 9.71800000e+03  2.11805000e+00  1.20621624e-02  2.29686900e-02
   5.89230502e-01]
 [ 9.71900000e+03  1.61018700e+00  1.76928041e-02  3.92033762e-02
   5.36947139e-01]
 [ 9.71900000e+03  1.41488000e-01  2.57416168e-02 -7.71452983e-03
   5.20508288e-01]]


#### end of manipulation

In [4]:
ll = []
true_vals = []
print(int(np.min(data,axis=0)[0]))
print(int(np.max(data,axis=0)[0]))

for i in range(int(np.min(data,axis=0)[0]),int(np.max(data,axis=0)[0])+1,3):
    print(i)
    mask = ((data[:,0] == i) | (data[:,0] == i+1) | (data[:,0] == i+2))
    print("This is mask:")
    print(mask)
    evt = data[mask]
    #print(evt)
    #print(evt.shape[0])
    pair_indices = list(combinations(range(evt.shape[0]), 2))
    print("pair indices...")
    print(pair_indices)
    for i, (idx1, idx2) in enumerate(pair_indices):
        l = []
        print("this are the pairs to be compared")
        print(evt[idx1,1:])
        print(evt[idx2,1:])
        ### this is the new stuff....
        time_diff = abs(evt[idx1,4]-evt[idx2,4])
        ene_diff = abs(evt[idx1,1]-evt[idx2,1])
        min_theta = evt[idx1,2] if evt[idx2,2] > evt[idx1,2] else evt[idx2,2]
        max_theta = evt[idx2,2] if evt[idx2,2] > evt[idx1,2] else evt[idx1,2]
        theta_diff = abs(max_theta-min_theta) if (abs(max_theta-min_theta) < abs(max_theta-(min_theta+math.pi))) else abs(max_theta-(min_theta+math.pi)) 
        min_phi = evt[idx1,3] if evt[idx2,3] > evt[idx1,3] else evt[idx2,3]
        max_phi = evt[idx2,3] if evt[idx2,3] > evt[idx1,3] else evt[idx1,3]
        phi_diff = abs(max_phi-min_phi) if (abs(max_phi-min_phi) < abs(max_phi-(min_phi+math.pi))) else abs(max_phi-(min_phi+math.pi))
        #print("energy diff",ene_diff)
        #print("time_diff\t",time_diff)
        #print("theta_diff\t",theta_diff)
        #print("phi_diff\t",phi_diff)
        diff_arr = np.array([ene_diff,theta_diff,phi_diff,time_diff])
        #print("diff_arr\t",diff_arr)
        test_np = np.concatenate((evt[idx1,1:],evt[idx2,1:]))
        #print("fooooo", test_np)
        test_np = np.concatenate((test_np,diff_arr))
        #print("final_arr:\t",test_np)
        #l.append(np.concatenate((evt[idx1,1:],evt[idx2,1:],diff_arr)))
        ### end of new stuff
        l.append(np.concatenate((evt[idx1,1:],evt[idx2,1:])))
        print(l)
        ll.append(l)
        if (evt[idx1,0] == evt[idx2,0]):
            true_vals.append(1)
        else:
            true_vals.append(0)
#print(ll)
input_data = torch.FloatTensor(ll)
input_data = torch.squeeze(input_data)
input_data.shape
truth_class = torch.FloatTensor(true_vals)
print(input_data.shape)
print(truth_class.shape)

0
9719
0
This is mask:
[ True  True  True ... False False False]
pair indices...
[(0, 1), (0, 2), (0, 3), (1, 2), (1, 3), (2, 3)]
this are the pairs to be compared
[ 1.128016    0.0159398  -0.04711988  0.32053203]
[0.952915   0.00906077 0.01533811 0.9308782 ]
[array([ 1.128016  ,  0.0159398 , -0.04711988,  0.32053203,  0.952915  ,
        0.00906077,  0.01533811,  0.9308782 ])]
this are the pairs to be compared
[ 1.128016    0.0159398  -0.04711988  0.32053203]
[ 0.434082    0.00990771 -0.0403509   0.91661279]
[array([ 1.128016  ,  0.0159398 , -0.04711988,  0.32053203,  0.434082  ,
        0.00990771, -0.0403509 ,  0.91661279])]
this are the pairs to be compared
[ 1.128016    0.0159398  -0.04711988  0.32053203]
[2.209619   0.01929406 0.04073043 0.54709982]
[array([ 1.128016  ,  0.0159398 , -0.04711988,  0.32053203,  2.209619  ,
        0.01929406,  0.04073043,  0.54709982])]
this are the pairs to be compared
[0.952915   0.00906077 0.01533811 0.9308782 ]
[ 0.434082    0.00990771 -0.04035

        0.00851595,  0.04976164,  0.27891398])]
this are the pairs to be compared
[ 0.281258    0.01560377 -0.00091333  0.68443405]
[1.817381   0.00851595 0.04976164 0.27891398]
[array([ 2.81258000e-01,  1.56037671e-02, -9.13330798e-04,  6.84434047e-01,
        1.81738100e+00,  8.51595011e-03,  4.97616408e-02,  2.78913984e-01])]
69
This is mask:
[False False False ... False False False]
pair indices...
[(0, 1), (0, 2), (0, 3), (1, 2), (1, 3), (2, 3)]
this are the pairs to be compared
[ 2.131801    0.01409193 -0.03869343  0.30902631]
[1.547512   0.02131988 0.02086281 0.93743148]
[array([ 2.131801  ,  0.01409193, -0.03869343,  0.30902631,  1.547512  ,
        0.02131988,  0.02086281,  0.93743148])]
this are the pairs to be compared
[ 2.131801    0.01409193 -0.03869343  0.30902631]
[0.492523   0.00991288 0.04212064 0.93549208]
[array([ 2.131801  ,  0.01409193, -0.03869343,  0.30902631,  0.492523  ,
        0.00991288,  0.04212064,  0.93549208])]
this are the pairs to be compared
[ 2.13180

[ 2.135111    0.02048034 -0.05233394  0.42491573]
[array([ 0.898789  ,  0.02436239, -0.00770956,  0.90961643,  2.135111  ,
        0.02048034, -0.05233394,  0.42491573])]
this are the pairs to be compared
[2.093797   0.0228675  0.01882763 0.32969275]
[ 2.135111    0.02048034 -0.05233394  0.42491573]
[array([ 2.093797  ,  0.0228675 ,  0.01882763,  0.32969275,  2.135111  ,
        0.02048034, -0.05233394,  0.42491573])]
141
This is mask:
[False False False ... False False False]
pair indices...
[(0, 1), (0, 2), (0, 3), (1, 2), (1, 3), (2, 3)]
this are the pairs to be compared
[ 1.4066      0.01558541 -0.01454191  0.64820586]
[ 2.116197    0.02172259 -0.05463484  0.57337449]
[array([ 1.4066    ,  0.01558541, -0.01454191,  0.64820586,  2.116197  ,
        0.02172259, -0.05463484,  0.57337449])]
this are the pairs to be compared
[ 1.4066      0.01558541 -0.01454191  0.64820586]
[1.11958    0.02237669 0.03686539 0.31051353]
[array([ 1.4066    ,  0.01558541, -0.01454191,  0.64820586,  1.11958

[0.267799   0.02285018 0.01652363 0.91860445]
[ 2.08457     0.00830737 -0.04970783  0.45798316]
[array([ 0.267799  ,  0.02285018,  0.01652363,  0.91860445,  2.08457   ,
        0.00830737, -0.04970783,  0.45798316])]
this are the pairs to be compared
[2.195199   0.01237979 0.00428251 0.6569962 ]
[ 2.08457     0.00830737 -0.04970783  0.45798316]
[array([ 2.195199  ,  0.01237979,  0.00428251,  0.6569962 ,  2.08457   ,
        0.00830737, -0.04970783,  0.45798316])]
210
This is mask:
[False False False ... False False False]
pair indices...
[(0, 1), (0, 2), (0, 3), (1, 2), (1, 3), (2, 3)]
this are the pairs to be compared
[2.11925    0.01701726 0.00430437 0.1872034 ]
[ 1.796397    0.02516313 -0.04107648  0.76812347]
[array([ 2.11925   ,  0.01701726,  0.00430437,  0.1872034 ,  1.796397  ,
        0.02516313, -0.04107648,  0.76812347])]
this are the pairs to be compared
[2.11925    0.01701726 0.00430437 0.1872034 ]
[1.09722    0.02158574 0.02296009 0.8300228 ]
[array([2.11925   , 0.01701726

        0.02225466, -0.04415044,  0.91124452])]
this are the pairs to be compared
[ 0.531025    0.01716142 -0.03346515  0.44918635]
[2.131886   0.01152909 0.04922549 0.28198043]
[array([ 0.531025  ,  0.01716142, -0.03346515,  0.44918635,  2.131886  ,
        0.01152909,  0.04922549,  0.28198043])]
this are the pairs to be compared
[ 2.137732    0.02225466 -0.04415044  0.91124452]
[2.131886   0.01152909 0.04922549 0.28198043]
[array([ 2.137732  ,  0.02225466, -0.04415044,  0.91124452,  2.131886  ,
        0.01152909,  0.04922549,  0.28198043])]
273
This is mask:
[False False False ... False False False]
pair indices...
[(0, 1), (0, 2), (0, 3), (1, 2), (1, 3), (2, 3)]
this are the pairs to be compared
[2.043627   0.02051956 0.01997196 0.88472922]
[ 2.10019     0.01921513 -0.0024876   0.3173906 ]
[array([ 2.043627  ,  0.02051956,  0.01997196,  0.88472922,  2.10019   ,
        0.01921513, -0.0024876 ,  0.3173906 ])]
this are the pairs to be compared
[2.043627   0.02051956 0.01997196 0.8847

...

       0.02271691, 0.01111965, 0.42176066])]
this are the pairs to be compared
[1.567165   0.01744987 0.00691885 0.89728473]
[ 2.083316    0.01525964 -0.04643014  0.11079552]
[array([ 1.567165  ,  0.01744987,  0.00691885,  0.89728473,  2.083316  ,
        0.01525964, -0.04643014,  0.11079552])]
this are the pairs to be compared
[ 0.507171    0.02323288 -0.03185695  0.92093355]
[1.646034   0.02271691 0.01111965 0.42176066]
[array([ 0.507171  ,  0.02323288, -0.03185695,  0.92093355,  1.646034  ,
        0.02271691,  0.01111965,  0.42176066])]
this are the pairs to be compared
[ 0.507171    0.02323288 -0.03185695  0.92093355]
[ 2.083316    0.01525964 -0.04643014  0.11079552]
[array([ 0.507171  ,  0.02323288, -0.03185695,  0.92093355,  2.083316  ,
        0.01525964, -0.04643014,  0.11079552])]
this are the pairs to be compared
[1.646034   0.02271691 0.01111965 0.42176066]
[ 2.083316    0.01525964 -0.04643014  0.11079552]
[array([ 1.646034  ,  0.02271691,  0.01111965,  0.42176066,  2.08331

[ 0.55133     0.0194278  -0.03186435  0.66321544]
[2.15977    0.01209016 0.01449581 0.81329651]
[array([ 0.55133   ,  0.0194278 , -0.03186435,  0.66321544,  2.15977   ,
        0.01209016,  0.01449581,  0.81329651])]
this are the pairs to be compared
[ 0.55133     0.0194278  -0.03186435  0.66321544]
[ 2.156572    0.00960439 -0.04727399  0.11179532]
[array([ 0.55133   ,  0.0194278 , -0.03186435,  0.66321544,  2.156572  ,
        0.00960439, -0.04727399,  0.11179532])]
this are the pairs to be compared
[2.15977    0.01209016 0.01449581 0.81329651]
[ 2.156572    0.00960439 -0.04727399  0.11179532]
[array([ 2.15977   ,  0.01209016,  0.01449581,  0.81329651,  2.156572  ,
        0.00960439, -0.04727399,  0.11179532])]
9609
This is mask:
[False False False ... False False False]
pair indices...
[(0, 1), (0, 2), (0, 3), (1, 2), (1, 3), (2, 3)]
this are the pairs to be compared
[2.14631    0.02363329 0.02136023 0.81523931]
[ 2.15193     0.02159377 -0.03952     0.18384496]
[array([ 2.14631   , 

[0.262271   0.02160335 0.01271404 0.86311183]
[0.763241   0.022365   0.02480467 0.21572626]
[array([0.262271  , 0.02160335, 0.01271404, 0.86311183, 0.763241  ,
       0.022365  , 0.02480467, 0.21572626])]
this are the pairs to be compared
[2.050775   0.01147694 0.01423766 0.53628193]
[0.763241   0.022365   0.02480467 0.21572626]
[array([2.050775  , 0.01147694, 0.01423766, 0.53628193, 0.763241  ,
       0.022365  , 0.02480467, 0.21572626])]
9669
This is mask:
[False False False ... False False False]
pair indices...
[(0, 1), (0, 2), (0, 3), (1, 2), (1, 3), (2, 3)]
this are the pairs to be compared
[1.45231000e+00 2.32522886e-02 8.97238862e-04 6.75581222e-01]
[0.314143   0.02075505 0.03529843 0.67770922]
[array([1.45231000e+00, 2.32522886e-02, 8.97238862e-04, 6.75581222e-01,
       3.14143000e-01, 2.07550540e-02, 3.52984289e-02, 6.77709218e-01])]
this are the pairs to be compared
[1.45231000e+00 2.32522886e-02 8.97238862e-04 6.75581222e-01]
[ 2.120725    0.0085108  -0.02531803  0.5555989

       0.0121729 , 0.03869072, 0.87809073])]
this are the pairs to be compared
[1.77702    0.00991282 0.01270793 0.87487999]
[ 0.3086      0.01698902 -0.03527659  0.88022555]
[array([ 1.77702   ,  0.00991282,  0.01270793,  0.87487999,  0.3086    ,
        0.01698902, -0.03527659,  0.88022555])]
this are the pairs to be compared
[1.77702    0.00991282 0.01270793 0.87487999]
[2.030897   0.0121729  0.03869072 0.87809073]
[array([1.77702   , 0.00991282, 0.01270793, 0.87487999, 2.030897  ,
       0.0121729 , 0.03869072, 0.87809073])]
this are the pairs to be compared
[ 0.3086      0.01698902 -0.03527659  0.88022555]
[2.030897   0.0121729  0.03869072 0.87809073]
[array([ 0.3086    ,  0.01698902, -0.03527659,  0.88022555,  2.030897  ,
        0.0121729 ,  0.03869072,  0.87809073])]
9690
This is mask:
[False False False ... False False False]
pair indices...
[(0, 1), (0, 2), (0, 3), (1, 2), (1, 3), (2, 3)]
this are the pairs to be compared
[ 2.053182    0.0118289  -0.04556592  0.28742029]
[2.1

/home/tobiasjenegger/jupy/jup_notebook/lib/python3.6/site-packages/ipykernel_launcher.py:51: UserWarning: Creating a tensor from a list of numpy.ndarrays is extremely slow. Please consider converting the list to a single numpy.ndarray with numpy.array() before converting to a tensor. (Triggered internally at  ../torch/csrc/utils/tensor_new.cpp:201.)


In [5]:
class two_hidden_layer_model(nn.Module):
        def __init__(self,nodes,hidden_nodes):
                super().__init__()
                self.linear = torch.nn.Linear(8,nodes)
                self.another_linear = torch.nn.Linear(nodes,hidden_nodes)
                self.another_linear_two = torch.nn.Linear(hidden_nodes,hidden_nodes)
                self.activation = torch.nn.ReLU()
                self.linear_back = torch.nn.Linear(hidden_nodes,1)

        def forward(self, x):
                output_tensor = self.linear(x)
                #output_tensor = self.another_linear(output_tensor)
                output_tensor = self.activation(output_tensor)
                output_tensor = self.another_linear(output_tensor)
                output_tensor = self.another_linear_two(output_tensor)
                output_tensor = self.linear_back(output_tensor)
                output_tensor = torch.sigmoid(output_tensor)
                output_tensor = torch.squeeze(output_tensor)
                return output_tensor

In [6]:
def run_two_hidden_model(features,learning_rate,hidden_features):
    n_epochs = 10000
    model = two_hidden_layer_model(features,hidden_features)
    loss_fn = nn.BCELoss()  # binary cross entropy
    optimizer = optim.SGD(model.parameters(), lr=learning_rate)
    model.train()
    loss_val = []
    for epoch in range(n_epochs):
        y_pred = model(input_data)
        y_true = truth_class
        loss = loss_fn(y_pred,y_true)
        loss_val.append(loss.detach().item())
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
        #print(f'Finished epoch {epoch}, latest loss {loss}')
    plt.plot(loss_val)
    print("this is latest loss val:\t",loss_val[-1])
    torch.save(model,"ff_scripted.pt")
    with torch.no_grad():
        model = torch.load("ff_scripted.pt")
        model.eval()
    eval_pred = model(input_data).detach().numpy()
    return eval_pred,loss_val[-1]

In [7]:
eval_pred_h2 = run_two_hidden_model(1000,5e-3,100)
eval_true = truth_class.detach().numpy()

KeyboardInterrupt: 

In [ ]:
energy_spec = []
unique_ind = np.unique(data[:,0])
print(unique_ind.shape[0])
for i in range(unique_ind.shape[0]):
    ene = np.sum(data[data[:,0] == i,1])
    print (ene)
    energy_spec.append(ene)

plt.hist(energy_spec)
plt.title("True energy spectrum")

print(eval_pred_h2[0].shape)
print(eval_pred_h2[0][1])

print(eval_pred_h2[0])

In [ ]:
import networkx as nx
print(data)
ene_list = []
idx = 0
for i in range(int(np.min(data,axis=0)[0]),int(np.max(data,axis=0)[0])+1,3):
    mask = ((data[:,0] == i) | (data[:,0] == i+1) | (data[:,0] == i+2))
    evt = data[mask]
    print(evt)
    pair_indices = list(combinations(range(evt.shape[0]), 2))
    print("pair indices...")
    print(pair_indices)
    ##pair indices which belong together...
    pred_comb = []
    for m in range(evt.shape[0]):
        pred_comb.append((m,m))
    for j in range (len(pair_indices)):
        if eval_pred_h2[0][idx+j] > 0.75:
            pred_comb.append(pair_indices[j])
    G = nx.Graph()
    G.add_edges_from(pred_comb)
    connected_components = list(nx.connected_components(G))
    print("Connected components:", connected_components)
    print(type(connected_components))
    for k in range(len(connected_components)):
        print("this is type of k:")
        columns_to_sum = evt[list(connected_components[k]),1]
        ene = np.sum(columns_to_sum)
        ene_list.append(ene)
        print(ene)
        print(type(connected_components[k]))
    idx += len(pair_indices)
single_hit_energies = []
for i in range(data.shape[0]):
    single_hit_energies.append(data[i,1])
    
#plt.hist(single_hit_energies,bins=100,range=(0,10),label="single hit energy",color="green",alpha=0.5)    
plt.hist(ene_list,bins=100,range=(0,10),label="reconstructed energy",color="red",alpha=0.3)
plt.hist(energy_spec,bins=100,range=(0,10),label="true energies",color="blue",alpha=0.3)
plt.legend()
plt.yscale('log')
plt.savefig("epoch100.png")
print(eval_pred_h2[0][1])

### look at the prediction plots

In [ ]:
eval_true = eval_true.astype(int)
pred_binaries = eval_pred_h2[0]
print(pred_binaries)

plt.hist(pred_binaries[eval_true == True],bins=100,range=(0,1),label="belonging together",color="red",alpha=0.5)
plt.hist(pred_binaries[eval_true == False],bins=100,range=(0,1),label="independent",color="blue",alpha=0.5)
#plt.yscale("log")
plt.grid()
plt.legend()
plt.savefig("pred_multi_layer_stuff.png")

### -------

In [ ]:
class feed_forward_model(nn.Module):
        def __init__(self,nodes):
                super().__init__()
                self.linear = torch.nn.Linear(8,nodes)
                #self.another_linear = torch.nn.Linear(100,100)
                self.activation = torch.nn.ReLU()
                self.linear_back = torch.nn.Linear(nodes,1)

        def forward(self, x):
                output_tensor = self.linear(x)
                #output_tensor = self.another_linear(output_tensor)
                output_tensor = self.activation(output_tensor)
                output_tensor = self.linear_back(output_tensor)
                output_tensor = torch.sigmoid(output_tensor)
                output_tensor = torch.squeeze(output_tensor)
                return output_tensor
def run_out_features(features):
    n_epochs = 10000                                             ##set default n_epochs = 1000
    loss_fn = nn.BCELoss()  # binary cross entropy
    loss_step_vals =[]
    model = feed_forward_model(int(features))
    #optimizer = optim.SGD(model.parameters(), lr=9e-3)  ##set default lr
    optimizer = optim.SGD(model.parameters(), lr=5e-3)
    model.train()
    loss_val = []
    for epoch in range(n_epochs):
        y_pred = model(input_data)
        y_true = truth_class
        loss = loss_fn(y_pred,y_true)
        loss_val.append(loss.detach().item())
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
    plt.plot(loss_val)
    print("this is latest loss val:\t",loss_val[-1])
    torch.save(model,"ff_scripted.pt")
    with torch.no_grad():
        model = torch.load("ff_scripted.pt")
        model.eval()
    eval_pred = model(input_data).detach().numpy()
    return eval_pred,loss_val[-1]





In [ ]:
eval_pred_h2 = run_out_features(10000)
eval_true = truth_class.detach().numpy()



In [ ]:
import networkx as nx
print(data)
ene_list = []
idx = 0
for i in range(int(np.min(data,axis=0)[0]),int(np.max(data,axis=0)[0])+1,3):
    mask = ((data[:,0] == i) | (data[:,0] == i+1) | (data[:,0] == i+2))
    evt = data[mask]
    print(evt)
    pair_indices = list(combinations(range(evt.shape[0]), 2))
    print("pair indices...")
    print(pair_indices)
    ##pair indices which belong together...
    pred_comb = []
    for m in range(evt.shape[0]):
        pred_comb.append((m,m))
    for j in range (len(pair_indices)):
        if eval_pred_h2[0][idx+j] > 0.65:
            pred_comb.append(pair_indices[j])
    G = nx.Graph()
    G.add_edges_from(pred_comb)
    connected_components = list(nx.connected_components(G))
    print("Connected components:", connected_components)
    print(type(connected_components))
    for k in range(len(connected_components)):
        print("this is type of k:")
        columns_to_sum = evt[list(connected_components[k]),1]
        ene = np.sum(columns_to_sum)
        ene_list.append(ene)
        print(ene)
        print(type(connected_components[k]))
    idx += len(pair_indices)
single_hit_energies = []
for i in range(data.shape[0]):
    single_hit_energies.append(data[i,1])
    
plt.hist(single_hit_energies,bins=100,range=(0,10),label="single hit energy",color="green",alpha=0.5)    
plt.hist(ene_list,bins=100,range=(0,10),label="reconstructed energy",color="red",alpha=0.3)
plt.hist(energy_spec,bins=100,range=(0,10),label="true energies",color="blue",alpha=0.3)
plt.legend()
plt.yscale('log')
plt.savefig("epoch100.png")
print(eval_pred_h2[0][1])

In [ ]:
eval_true = eval_true.astype(int)
pred_binaries = eval_pred_h2[0]
print(pred_binaries)

plt.hist(pred_binaries[eval_true == True],bins=100,range=(0,1),label="belonging together",color="red",alpha=0.5)
plt.hist(pred_binaries[eval_true == False],bins=100,range=(0,1),label="independent",color="blue",alpha=0.5)
plt.yscale("log")
plt.grid()
plt.legend()
plt.savefig("pred_val_distr_single_layer12_features.png")

In [ ]:
eval_true.shape
eval_true = eval_true.astype(int)
print(eval_true)